In [ ]:
# ..... get cell types using Feng et al markers ..... #

In [3]:
library(SingleCellExperiment)
library(MetaMarkers)
library(Seurat)
library(data.table)
library(dplyr)

In [4]:
# load list of orthologs
om = read.delim('lizard_mouse_orthologs_eggNOG.txt', sep = '\t')
om <- om[!is.na(om$lizard_gene) & !is.na(om$ortholog_name),]
dim(om)
om[1,]

[1] 27248     7

query          orth_type species             orthologs          lizard_gene
1 XP_060608688.1 one2one   Mus musculus(10090) ENSMUSP00000081225 ARHGEF10   
  ortholog_gene      ortholog_name
1 ENSMUSG00000071176 Arhgef10

In [5]:
# list of stages and samples
stages = rep(c('stage9', 'stage13', 'stage16'), each = 3)
samples = paste0('sample', rep(1:3, 3))

In [6]:
# function to get top 100 markers for each cell type
get_top_markers <- function(markers, ctypes){
    markers$rank = NA
    for(ii in 1:length(ctypes)){
        id = which(markers$cell_type==ctypes[ii])
        markers$rank[id] = 1:length(id)
    }
    return(markers)
}

In [7]:
# load class markers
markers = fread('~/septation/markers/Feng/Feng_minor_celltype_markers_E10.5_E14.5.csv.gz')
markers$gene <- om$lizard_gene[match(markers$gene, om$ortholog_name)]
markers <- markers[!is.na(markers$gene),]
ctypes = unique(markers$cell_type)

# get rank of markers
markers = get_top_markers(markers, ctypes)

# tibble of group, cell_type, gene, rank
top_markers = as_tibble(markers[which(markers$rank<=100),c('group', 'cell_type', 'gene')])
top_markers[1:2,]

group cell_type gene
1 all   atrial_cm MYL1
2 all   atrial_cm MYL7

In [8]:
# get cell type anno
pb = txtProgressBar(min = 0, max = length(samples), initial = 0)

for(id in 1:length(samples)){
    
    # load seurat object
    sce = readRDS(paste0(stages[id], '_', samples[id], '_data.rds'))

    # get SCE object
    sc3 = SingleCellExperiment(list(counts = LayerData(sce, assay = 'RNA', layer = 'counts')))
    colData(sc3) <- DataFrame(sce@meta.data)
    assay(sc3, "cpm") = convert_to_cpm(assay(sc3))
    
    # predict cell type neighborhood
    ct_scores = score_cells(log1p(cpm(sc3)), top_markers)
    ct_enrichment = compute_marker_enrichment(ct_scores)
    ct_pred = assign_cells(ct_scores)
    
    # save
    write.table(ct_pred, file = paste0('annotations/', stages[id], '_', samples[id], '_Feng_celltypes.csv'),
            sep = ',', row.names = T, col.names = T, quote = F)
    
    setTxtProgressBar(pb, id)
}